In [1]:
import statsmodels.api as sm
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import LabelEncoder       # instantiate labelencoder object
from sklearn.preprocessing import StandardScaler

from sklearn.feature_extraction import DictVectorizer
from sklearn.feature_selection import SelectKBest   #feature selection best features
from sklearn.feature_selection import chi2         # clase chi-cuadrado 
from sklearn.feature_selection import f_classif, f_regression    #clase f_clasificador ANOVA
from sklearn.feature_selection import RFE, SelectFromModel

from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold, cross_val_score
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import RidgeCV, LassoCV, Ridge, Lasso
from sklearn.linear_model import LogisticRegression, Perceptron

from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from sklearn.svm import LinearSVC

from sklearn.externals import joblib

from sklearn.metrics import r2_score
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn import metrics 
pd.set_option('display.max_rows', 4706)

In [32]:
df = pd.read_csv('/data/DWeb/inguat-backend/data/Inguat_isnull.csv', index_col=0)
df.head()

SEC_INT  P1                                     P2$01  \
0  1010084  Si                     Vacaciones personales   
1  1010084  Si                     Vacaciones personales   
3  1010084  Si                     Vacaciones personales   
4  1010084  Si                     Vacaciones personales   
6  1010084  Si  Día de la independencia 15 de septiembre   

                               P4 DEPTO_MUNI  P7_NO_PERNOC  P7_SI_PERNOC  \
0  No dispone de segunda vivienda    NINGUNO           3.0           6.0   
1  No dispone de segunda vivienda    NINGUNO           3.0           5.0   
3  No dispone de segunda vivienda    NINGUNO           3.0          10.0   
4  No dispone de segunda vivienda    NINGUNO           3.0           0.0   
6  No dispone de segunda vivienda    NINGUNO           3.0          10.0   

   P9_#EXCURSION                                        DEP_MUN_LUG  \
0            1.0  SACATEPEQUEZ_ANTIGUA GUATEMALA_CONVENTO LAS CA...   
1            1.0  SACATEPEQUEZ_ANTIGUA GUATEMALA_CONVENTO LAS CA...   
3            1.0                                              FALSO   
4            1.0                                              FALSO   
6            1.0                                              FALSO   

          P11_MOTIVO_EXCURSION  \
0  Ocio, recreo y/o vacaciones   
1  Ocio, recreo y/o vacaciones   
3  Ocio, recreo y/o vacaciones   
4  Ocio, recreo y/o vacaciones   
6  Ocio, recreo y/o vacaciones   

                        ...                        VIA_VIAJE  P18_#NOCHES1  \
0                       ...                               Sí           4.0   
1                       ...                               No           1.0   
3                       ...                               Sí           1.0   
4                       ...                               No           1.0   
6                       ...                               Sí           4.0   

   P19_#PERSON1                 P20_MOTIVO_1                   P21_ALOJ_1  \
0           4.0  Ocio, recreo y/o vacaciones  Casa de amigos o familiares   
1           4.0  Ocio, recreo y/o vacaciones            Hotel o similares   
3           8.0  Ocio, recreo y/o vacaciones            Hotel o similares   
4           4.0  Ocio, recreo y/o vacaciones            Hotel o similares   
6           5.0  Ocio, recreo y/o vacaciones            Hotel o similares   

  P22_PER_GAS_1  P24_VIAJE_ORG  P26_TRASPORTE P27_DG_SUMA  \
0           4.0  Por su cuenta  Bus turístico       850.0   
1           4.0  Por su cuenta       Vehículo         0.0   
3           8.0  Por su cuenta       Vehículo         0.0   
4           4.0  Por su cuenta       Vehículo         0.0   
6           5.0  Por su cuenta       Vehículo      2000.0   

                                     P17_DESTINO1  
0             TOTONICAPAN_MOMOSTENANGO_LOS RISCOS  
1                  CHIQUIMULA_ESQUIPULAS_BASILICA  
3     CHIQUIMULA_ESQUIPULAS_IGLESIA DE ESQUIPULAS  
4                  CHIQUIMULA_ESQUIPULAS_BASILICA  
6  QUETZALTENANGO_QUETZALTENANGO_CENTRO HISTORICO  

[5 rows x 28 columns]

In [16]:
ds = pd.read_csv('/data/sample_test.csv', index_col=0)
el = EncoderXY()
ds_el= el.fit_transform(ds)
ds_el= ds_el.drop(['DEP_MUN_LUG'], axis=1)
ds_el. shape

(3, 27)

In [43]:
clf =  joblib.load('/data/DWeb/inguat-backend/model/RF_model.joblib')
pred = clf.predict(ds_el)
pred

array([ 61, 419, 526])

In [44]:
ydef = pd.read_csv('/data/DWeb/inguat-backend/data/y_definitions.csv', index_col=0)
le= LabelEncoder()
ydef_enc =le.fit_transform(ydef)
ydef_enc

/home/itsky/anaconda3/lib/python3.7/site-packages/sklearn/preprocessing/label.py:235: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


array([428, 153, 153, ..., 137, 137, 137])

In [45]:
labels_pred = le.inverse_transform(ydef_enc)
pred_df = pd.Series(labels_pred)
pred_df.value_counts()

FALSO                                                                                 1589
SACATEPEQUEZ_ANTIGUA GUATEMALA_CENTRO HISTORICO                                        115
ESCUINTLA_SAN JOSE_PUERTO SAN JOSE                                                      62
SACATEPEQUEZ_ANTIGUA GUATEMALA_ANTIGUA GUATEMALA                                        52
QUETZLATENANGO_QUETZALTENANGO_CENTRO HISTORICO                                          27
GUATEMALA_GUATEMALA_GUATEMALA                                                           26
GUATEMALA_GUATEMALA_CENTRO HISTORICO                                                    25
SOLOLÁ_PANAJACHEL_LAGO DE ATITLAN                                                       24
SOLOLÁ_PANAJACHEL_LAGO                                                                  21
CHIMALTENANGO_TECPAN_TECPAN                                                             19
ZACAPA_RIO HONDO_VALLE DORADO                                                           19

In [12]:
class EncoderXY:
    def __init__(self, columns = None ):
        self.columns = columns    # lista de columnas a codificar

    def fit(self, X, y = None):
        return self

    def transform(self, X):
        '''
        transforma las columnas de X especificadas en self.columns usando Label_encoder().
        Si no se especifica transforma todas las columans de X
        '''
        salida = X.copy()

        if self.columns is not None:
            for col in self.columns:
                salida[col] = LabelEncoder().fit_transform(salida[col])
        else:
            for colname, col in salida.items():
                salida[colname] = LabelEncoder().fit_transform(col)

        return salida

    def fit_transform(self, X, y=None):
        return self.fit(X, y).transform(X)

##  ds_le => Usando LabelEncoder   ds_dict => USando DictVectorizer

In [9]:
LEncoder = EncoderXY()
ds_le = LEncoder.fit_transform(ds)


#-----------------------DICTVECTOR
ds_dict = ds.to_dict(orient='records')

DV = DictVectorizer(sparse=False)
ds_dvector = DV.fit_transform(ds_dict)
#ds_dvector

#-----------------------------------------------------------
#df_corr_health = ds_dvector.corr()['DEP_MUN_LUG'].sort_values(ascending=False).head(26)
#top_corr_features = df_corr_health.index# plot top 20 most correlated features to our target (HEALTH)
#df_corr_health.plot(kind='barh')


In [12]:
#---------------------SPLIT con LEncoder
X_le = ds_le.drop(columns='DEP_MUN_LUG')  
y_le = ds_le['DEP_MUN_LUG'].copy()  
#print(y_le.head())

#---------------------SPLIT con DVECTORIZER
#X_dv = ds_dvector.drop(columns='DEP_MUN_LUG')  
#y_dv = ds_dvector['DEP_MUN_LUG'].copy() 
#pd.Series({'data':np.array(ds_dvector)}).value_counts()


X_le

Unnamed: 0  SEC_INT  P1  P2$01  P4  DEPTO_MUNI  P7_NO_PERNOC  \
0              0        1   0     14   0         102             2   
1              1        1   0     14   0         102             2   
2              2        1   0     14   0         102             2   
3              3        1   0     14   0         102             2   
4              4        1   0      3   0         102             2   
5              5        1   0      3   0         102             2   
6              6        2   0      9   1         133             2   
7              7        2   0      9   1         133             2   
8              8        2   0      9   1         133             2   
9              9      219   0      0   0         102             2   
10            10      219   0      0   0         102             2   
11            11      219   0      0   0         102             2   
12            12      219   0      2   0         102             2   
13            13      219   0      2   0         102             2   
14            14      219   0     14   0         102             2   
15            15      219   0     14   0         102             2   
16            16      219   0      5   2          41            10   
17            17      219   0      5   2          41            10   
18            18      219   0      1   0         102             2   
19            19      219   0      1   0         102             2   
20            20      251   0      2   0         102             2   
21            21      251   0      2   0         102             2   
22            22      251   0      2   0         102             2   
23            23      251   0      6   1         167             2   
24            24      251   0      6   1         167             2   
25            25      177   0      9   0         102             2   
26            26      177   0      9   0         102             2   
27            27      177   0      4   0         102             2   
28            28      177   0      4   0         102             2   
29            29      177   0      4   0         102             2   
30            30      177   0     14   0         102             2   
31            31      177   0     14   0         102             2   
32            32      177   0      5   1         129             2   
33            33      177   0      5   1         129             2   
34            34      177   0      5   1         129             2   
35            35      190   0      9   0         102             2   
36            36      190   0      9   0         102             2   
37            37      190   0      9   0         102             2   
38            38      190   0      6   1          84             2   
39            39      190   0      6   1          84             2   
40            40      190   0      6   1          84             2   
41            41      190   0     12   0         102             2   
42            42      190   0     12   0         102             2   
43            43      190   0     11   0         102             2   
44            44      190   0     11   0         102             2   
45            45      190   0      2   0         102             2   
46            46      190   0      2   0         102             2   
47            47      190   0      4   0         102             2   
48            48      190   0      4   0         102             2   
49            49      190   0      4   0         102             2   
50            50      190   0     11   1         151             0   
51            51      190   0     11   1         151             0   
52            52      190   0     11   1         151             0   
53            53      184   0     11   0         102             2   
54            54      184   0     11   0         102             2   
55            55      184   0      5   0         102             2   
56            56

In [19]:
X_le.to_csv('X_le.csv')

In [20]:
#X_le = X_le.drop(['Unnamed: 0', 'P1'], axis=1)
y_le.head()

0    428
1    428
2    153
3    153
4    153
Name: DEP_MUN_LUG, dtype: int64

In [13]:
ppn = Perceptron(penalty='l2', alpha=0.0001, fit_intercept=True, max_iter=1000, tol=0.001, shuffle=True, 
                 verbose=0, eta0=1.0, n_jobs=-1, random_state=1, early_stopping=False, validation_fraction=0.1, 
                 n_iter_no_change=95, class_weight=None, warm_start=False).fit(X_le, y_le)

model_ppn = SelectFromModel(ppn, prefit=True)
X_new = model_ppn.transform(X_le)

features_ppn=X_le.columns[model_ppn.get_support(indices=True)]
features_ppn

Index(['Unnamed: 0', 'SEC_INT', 'DEPTO_MUNI', 'PROFESION', 'OCUPACION',
       'P27_DG_SUMA', 'P17_DESTINO1'],
      dtype='object')

In [30]:
lsvc = LinearSVC(C=0.01, penalty="l1", dual=False,max_iter=2000).fit(X_le, y_le) 
model_lsvc = SelectFromModel(lsvc, prefit=True)
feat_sel_lsvc = model_lsvc.transform(X_le)

feat_sel_lsvc=X_le.columns[model_lsvc.get_support(indices=True)]
feat_sel_lsvc

Index(['SEC_INT', 'P2$01', 'DEPTO_MUNI', 'P7_NO_PERNOC', 'P7_SI_PERNOC',
       'P9_#EXCURSION', 'P11_MOTIVO_EXCURSION', 'P13_GASTO_EXCURSION',
       'P14_#PER_EXCURSION', 'P16_#EXCUR_CONPERNOC', 'SUMA_PUNTOS', 'EDAD',
       'PROFESION', 'OCUPACION', 'P18_#NOCHES1', 'P19_#PERSON1',
       'P20_MOTIVO_1', 'P21_ALOJ_1', 'P22_PER_GAS_1', 'P24_VIAJE_ORG',
       'P26_TRASPORTE', 'P27_DG_SUMA', 'P17_DESTINO1'],
      dtype='object')

In [16]:
rf = RandomForestClassifier(n_estimators=200, criterion='entropy', max_depth=None, min_samples_split=2, 
                            min_samples_leaf=1, min_weight_fraction_leaf=0.0, max_features='sqrt', 
                            max_leaf_nodes=None, min_impurity_decrease=0.0, min_impurity_split=None, 
                            bootstrap=True, oob_score=True, n_jobs=None, random_state=None, verbose=0, 
                            warm_start=True, class_weight=None).fit(X_le, y_le)
model_rf = SelectFromModel(rf, prefit=True)
feat_sel_rf = model_rf.transform(X_le)

feat_sel_rf = X_le.columns[model_rf.get_support(indices=True)]
feat_sel_rf

Index(['Unnamed: 0', 'SEC_INT', 'P2$01', 'P9_#EXCURSION',
       'P11_MOTIVO_EXCURSION', 'P13_GASTO_EXCURSION', 'P14_#PER_EXCURSION',
       'SUMA_PUNTOS', 'EDAD', 'PROFESION', 'OCUPACION'],
      dtype='object')

In [17]:
ds_selected_rf = X_le.loc[:,feat_sel_rf]
ds_selected_rf.head()

Unnamed: 0  SEC_INT  P2$01  P9_#EXCURSION  P11_MOTIVO_EXCURSION  \
0           0        1     14              0                     1   
1           1        1     14              0                     1   
2           2        1     14              0                     1   
3           3        1     14              0                     1   
4           4        1      3              0                     1   

   P13_GASTO_EXCURSION  P14_#PER_EXCURSION  SUMA_PUNTOS  EDAD  PROFESION  \
0                   25                   4           10    37        515   
1                   25                   4           10    37        515   
2                   27                   3            7    54        227   
3                   27                   3            7    54        227   
4                   27                   3           17    32        243   

   OCUPACION  
0         35  
1         35  
2         35  
3         35  
4        204

In [18]:
X_train, X_test, y_train, y_test = train_test_split(ds_selected_rf, y_le, test_size=0.275, random_state=0)
print(X_train.shape, y_train.shape)
print(X_test.shape, y_test.shape)

(2588, 11) (2588,)
(983, 11) (983,)


In [19]:
scaler = StandardScaler()
scaler.fit(X_train)   # standarizando todo el ds con Lencoder

X_train_std = scaler.transform(X_train)
X_test_std = scaler.transform(X_test)


/home/itsky/anaconda3/lib/python3.7/site-packages/sklearn/preprocessing/data.py:625: DataConversionWarning: Data with input dtype int64 were all converted to float64 by StandardScaler.
  return self.partial_fit(X, y)
/home/itsky/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: DataConversionWarning: Data with input dtype int64 were all converted to float64 by StandardScaler.
  after removing the cwd from sys.path.
/home/itsky/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: DataConversionWarning: Data with input dtype int64 were all converted to float64 by StandardScaler.
  """


In [57]:
ppn = Perceptron(penalty='l1', alpha=0.0001, fit_intercept=True, max_iter=1000, tol=0.001, shuffle=True, 
                 verbose=1, eta0=1.0, n_jobs=-1, random_state=1, early_stopping=False, validation_fraction=0.1, 
                 n_iter_no_change=5, class_weight=None, warm_start=False)
ppn.fit(X_train_std, y_train)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.


-- Epoch 1
Norm: 4.26, NNZs: 9, Bias: -9.000000, T: 2588, Avg. loss: 0.015047
Total training time: 0.00 seconds.
-- Epoch 2
-- Epoch 1
Norm: 6.20, NNZs: 9, Bias: -10.000000, T: 2588, Avg. loss: 0.012575
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 7.91, NNZs: 7, Bias: -11.000000, T: 5176, Avg. loss: 0.007759
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 8.96, NNZs: 8, Bias: -11.000000, T: 7764, Avg. loss: 0.006352
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 8.80, NNZs: 9, Bias: -12.000000, T: 10352, Avg. loss: 0.000859
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 9.22, NNZs: 7, Bias: -13.000000, T: 12940, Avg. loss: 0.003919
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 5.22, NNZs: 4, Bias: -9.000000, T: 5176, Avg. loss: 0.006460
Total training time: 0.01 seconds.
-- Epoch 3
Norm: 6.77, NNZs: 7, Bias: -8.000000, T: 7764, Avg. loss: 0.005811
Total training time: 0.01 seconds.
-- Epoch 4
Norm: 8.92, NNZs: 6, Bias: -9.000000, T: 10352, Avg. loss: 0.002954

Norm: 5.86, NNZs: 9, Bias: -9.000000, T: 5176, Avg. loss: 0.013411
Total training time: 0.01 seconds.
-- Epoch 3
Norm: 8.72, NNZs: 7, Bias: -11.000000, T: 7764, Avg. loss: 0.012252
Total training time: 0.01 seconds.
-- Epoch 4
Norm: 9.96, NNZs: 7, Bias: -12.000000, T: 10352, Avg. loss: 0.011807
Total training time: 0.01 seconds.
-- Epoch 5
Norm: 11.75, NNZs: 7, Bias: -12.000000, T: 12940, Avg. loss: 0.007549
Total training time: 0.01 seconds.
-- Epoch 6
Norm: 12.99, NNZs: 7, Bias: -14.000000, T: 15528, Avg. loss: 0.006968
Total training time: 0.01 seconds.
-- Epoch 7
Norm: 14.15, NNZs: 6, Bias: -14.000000, T: 18116, Avg. loss: 0.007245
Total training time: 0.01 seconds.
-- Epoch 8
Norm: 15.29, NNZs: 5, Bias: -16.000000, T: 20704, Avg. loss: 0.009333
Total training time: 0.01 seconds.
-- Epoch 9
Norm: 15.89, NNZs: 7, Bias: -16.000000, T: 23292, Avg. loss: 0.007745
Total training time: 0.01 seconds.
-- Epoch 10
Norm: 16.93, NNZs: 8, Bias: -18.000000, T: 25880, Avg. loss: 0.009434
Total t

[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.4s


Norm: 9.47, NNZs: 9, Bias: -13.000000, T: 15528, Avg. loss: 0.006603
Total training time: 0.01 seconds.
-- Epoch 7
Norm: 9.80, NNZs: 8, Bias: -13.000000, T: 18116, Avg. loss: 0.002813
Total training time: 0.01 seconds.
-- Epoch 8

Norm: 10.81, NNZs: 8, Bias: -12.000000, T: 20704, Avg. loss: 0.002772
Total training time: 0.01 seconds.Norm: 6.56, NNZs: 6, Bias: -10.000000, T: 5176, Avg. loss: 0.004903
Total training time: 0.00 seconds.
-- Epoch 3

-- Epoch 9
Norm: 9.07, NNZs: 8, Bias: -11.000000, T: 7764, Avg. loss: 0.010300
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 11.30, NNZs: 8, Bias: -13.000000, T: 23292, Avg. loss: 0.001750
Total training time: 0.01 seconds.
-- Epoch 10
Norm: 12.75, NNZs: 10, Bias: -13.000000, T: 25880, Avg. loss: 0.004326
Total training time: 0.01 seconds.
-- Epoch 11
Norm: 12.60, NNZs: 9, Bias: -14.000000, T: 28468, Avg. loss: 0.002124
Total training time: 0.01 seconds.
-- Epoch 12
Norm: 12.86, NNZs: 8, Bias: -14.000000, T: 31056, Avg. loss: 0.002398
Tot

...

Norm: 19.32, NNZs: 9, Bias: -27.000000, T: 23292, Avg. loss: 0.005792
Total training time: 0.01 seconds.
-- Epoch 10
-- Epoch 1
Norm: 3.61, NNZs: 8, Bias: -7.000000, T: 2588, Avg. loss: 0.010530
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 5.15, NNZs: 10, Bias: -9.000000, T: 5176, Avg. loss: 0.003921
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 5.53, NNZs: 7, Bias: -9.000000, T: 7764, Avg. loss: 0.003587
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 6.73, NNZs: 6, Bias: -8.000000, T: 10352, Avg. loss: 0.002491
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 6.54, NNZs: 5, Bias: -9.000000, T: 12940, Avg. loss: 0.002722
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 20.39, NNZs: 7, Bias: -29.000000, T: 25880, Avg. loss: 0.017718
Total training time: 0.02 seconds.
-- Epoch 11
Norm: 21.89, NNZs: 6, Bias: -31.000000, T: 28468, Avg. loss: 0.017229
Total training time: 0.02 seconds.
-- Epoch 12
Norm: 23.32, NNZs: 7, Bias: -30.000000, T: 31056, Avg. loss: 0.004580


Norm: 27.26, NNZs: 4, Bias: -5.000000, T: 28468, Avg. loss: 0.022999
Total training time: 0.01 seconds.
-- Epoch 12
-- Epoch 1
Norm: 28.76, NNZs: 5, Bias: -6.000000, T: 31056, Avg. loss: 0.022768
Total training time: 0.01 seconds.
-- Epoch 13
Norm: 3.54, NNZs: 9, Bias: -10.000000, T: 2588, Avg. loss: 0.007817
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 30.40, NNZs: 2, Bias: -5.000000, T: 33644, Avg. loss: 0.022480
Total training time: 0.01 seconds.
-- Epoch 14
Norm: 5.53, NNZs: 8, Bias: -9.000000, T: 5176, Avg. loss: 0.003161
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 31.97, NNZs: 4, Bias: -7.000000, T: 36232, Avg. loss: 0.024456
Total training time: 0.01 seconds.
-- Epoch 15
Norm: 6.65, NNZs: 8, Bias: -12.000000, T: 7764, Avg. loss: 0.004186
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 33.49, NNZs: 4, Bias: -5.000000, T: 38820, Avg. loss: 0.022245
Total training time: 0.01 seconds.
Convergence after 15 epochs took 0.01 seconds
Norm: 7.18, NNZs: 6, Bias: -13.000

Norm: 11.97, NNZs: 6, Bias: -14.000000, T: 15528, Avg. loss: 0.005842
Total training time: 0.01 seconds.
-- Epoch 7
Norm: 4.96, NNZs: 9, Bias: -10.000000, T: 5176, Avg. loss: 0.008080
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 12.53, NNZs: 6, Bias: -14.000000, T: 18116, Avg. loss: 0.010245
Total training time: 0.01 seconds.
Norm: 6.81, NNZs: 8, Bias: -10.000000, T: 7764, Avg. loss: 0.005122
Total training time: 0.00 seconds.
-- Epoch 4
-- Epoch 8
Norm: 9.42, NNZs: 9, Bias: -11.000000, T: 10352, Avg. loss: 0.010353
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 13.24, NNZs: 3, Bias: -14.000000, T: 20704, Avg. loss: 0.006999
Total training time: 0.01 seconds.
Convergence after 8 epochs took 0.01 seconds
Norm: 9.27, NNZs: 8, Bias: -13.000000, T: 12940, Avg. loss: 0.004062
Total training time: 0.01 seconds.
-- Epoch 6
-- Epoch 1
Norm: 11.11, NNZs: 5, Bias: -15.000000, T: 15528, Avg. loss: 0.007020
Total training time: 0.01 seconds.
-- Epoch 7
Norm: 12.29, NNZs: 5, Bias: -14.0

[Parallel(n_jobs=-1)]: Done 542 out of 542 | elapsed:    4.3s finished


Perceptron(alpha=0.0001, class_weight=None, early_stopping=False, eta0=1.0,
      fit_intercept=True, max_iter=1000, n_iter=None, n_iter_no_change=5,
      n_jobs=-1, penalty='l1', random_state=1, shuffle=True, tol=0.001,
      validation_fraction=0.1, verbose=1, warm_start=False)

In [58]:
y_pred_ppn = ppn.predict(X_test_std)
print('Misclassified samples: %d' % (y_test != y_pred_ppn).sum())
print('Accuracy: %.2f' % accuracy_score(y_test, y_pred_ppn))

Misclassified samples: 559
Accuracy: 0.43


In [20]:
rf = RandomForestClassifier(n_estimators=200, criterion='gini', max_depth=None, min_samples_split=2, 
                            min_samples_leaf=1, min_weight_fraction_leaf=0.0, max_features='sqrt', 
                            max_leaf_nodes=None, min_impurity_decrease=0.0, min_impurity_split=None, 
                            bootstrap=True, oob_score=True, n_jobs=None, random_state=None, verbose=0, 
                            warm_start=True, class_weight=None)
rf.fit(X_train_std, y_train)


RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='sqrt', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=200, n_jobs=None,
            oob_score=True, random_state=None, verbose=0, warm_start=True)

In [21]:
y_predRF = rf.predict(X_test_std)
print('Misclassified samples: %d' % (y_test != y_predRF).sum())
print('Accuracy: %.2f' % accuracy_score(y_test, y_predRF))

Misclassified samples: 100
Accuracy: 0.90


In [44]:
svc = SVC(C=2.0, cache_size=200, class_weight=None, coef0=40.0, decision_function_shape='ovo', degree=3, gamma=0.020, 
          kernel='poly',max_iter=-1, probability=True, random_state=12, shrinking=True,tol=0.00001, verbose=False)
svc.fit(X_train_std, y_train)
y_pred_svc = svc.predict(X_test_std)
print('Punteo de Precisión ==>>', accuracy_score(y_pred_svc, y_test))

Punteo de Precisión ==>> 0.884028484231943


In [47]:
knn = KNeighborsClassifier(n_neighbors=395, weights='distance', algorithm='auto', leaf_size=60, p=1, 
                           metric='minkowski', metric_params=None, n_jobs=None)
knn.fit(X_train_std, y_train)


KNeighborsClassifier(algorithm='auto', leaf_size=60, metric='minkowski',
           metric_params=None, n_jobs=None, n_neighbors=395, p=1,
           weights='distance')

In [48]:
y_pred_knn = knn.predict(X_test_std)
print('Punteo de Precisión ==>>', accuracy_score(y_pred_knn, y_test))

Punteo de Precisión ==>> 0.8942014242115972


0       428
1       428
2       153
3       153
4       153
5       153
6       153
7       153
8       153
9        75
10       75
11       75
12      153
13      153
14      153
15      153
16       73
17       73
18       95
19       95
20      129
21      129
22      129
23      137
24      137
25      246
26      246
27      226
28      226
29      226
30      457
31      457
32      153
33      153
34      153
35      153
36      153
37      153
38      405
39      405
40      405
41      153
42      153
43      332
44      332
45      153
46      153
47      463
48      463
49      463
50      517
51      517
52      517
53      452
54      452
55      153
56      153
57      153
58      153
59      153
60      153
61      153
62      153
63      153
64      153
65      153
66      153
67       36
68       36
69      153
70      153
71      153
72      384
73      384
74      153
75      153
76      413
77      413
78      377
79      377
80      153
81      153
82      153
83  

In [22]:
le = LabelEncoder()
ds['destino_enc'] = le.fit_transform(ds['DEP_MUN_LUG'])

ds[['DEP_MUN_LUG','destino_enc']].head()

DEP_MUN_LUG  destino_enc
0  SACATEPEQUEZ_ANTIGUA GUATEMALA_CONVENTO LAS CA...          428
1  SACATEPEQUEZ_ANTIGUA GUATEMALA_CONVENTO LAS CA...          428
2                                              FALSO          153
3                                              FALSO          153
4                                              FALSO          153

In [23]:
labels_pred = le.inverse_transform(y_predRF)

#unique_elements, counts_elements = np.unique(labels_knn, return_counts=True)
pred_df = pd.Series(labels_pred)
pred_df.value_counts()

FALSO                                                                                 442
SACATEPEQUEZ_ANTIGUA GUATEMALA_CENTRO HISTORICO                                        44
ESCUINTLA_SAN JOSE_PUERTO SAN JOSE                                                     23
SACATEPEQUEZ_ANTIGUA GUATEMALA_ANTIGUA GUATEMALA                                       13
GUATEMALA_GUATEMALA_GUATEMALA                                                          10
CHIQUMULA_ESQUIPULAS_BASILICA                                                           9
GUATEMALA_GUATEMALA_CENTRO COMERCIAL                                                    8
SOLOLÁ_PANAJACHEL_LAGO DE ATITLAN                                                       8
GUATEMALA_GUATEMALA_CENTRO HISTORICO                                                    8
GUATEMALA_GUATEMALA_IRTRA PETAPA                                                        7
GUATEMALA_GUATEMALA_ZOOLOGICO                                                           7
QUETZLATEN